In [ ]:
df = load_dataset()
local_store_df = get_local_stores(df, country_code = "AE")

In [ ]:
local_store_df.sample(n=10).reset_index(drop=True)

In [ ]:
from sentiment_analysis import *

In [1]:
country_codes = ["AE", "CN", "NZ", "TH", "US"]

In [2]:
from util import *

for country_code in country_codes:
    print(get_country_dict(load_dataset())[country_code])

{'name': 'United Arab Emirates', 'n_stores': 68}
{'name': 'China', 'n_stores': 454}
{'name': 'New Zealand', 'n_stores': 22}
{'name': 'Thailand', 'n_stores': 121}
{'name': 'United States', 'n_stores': 9145}


In [6]:
from distribution_center import DistributionCenter
us_distrib_center = DistributionCenter(country_code="CN")
us_distrib_center.solve(method="nearest-neighbour") # held-karp

In [7]:
display(us_distrib_center.plot())

In [8]:
from distribution_center import DistributionCenter
us_distrib_center = DistributionCenter(country_code="US")
us_distrib_center.solve(method="nearest-neighbour") # held-karp

C:\Users\Jia Herng\Desktop\algo_proj\Moonbucks-G1\distribution_center.py:119: UserWarning: No route found, use geodesic distance
  warnings.warn("No route found, use geodesic distance")


In [9]:
print(us_distrib_center.info())
display(us_distrib_center.plot())

{'cost': 48729.30340901456, 'delivery_route': [58, 29, 11, 59, 80, 21, 10, 72, 42, 9, 92, 2, 69, 44, 15, 32, 1, 81, 63, 64, 65, 0, 17, 94, 27, 84, 7, 77, 87, 83, 61, 71, 20, 62, 52, 23, 98, 66, 41, 73, 13, 89, 78, 68, 86, 97, 33, 53, 30, 12, 74, 75, 95, 35, 46, 14, 19, 8, 25, 50, 38, 18, 88, 37, 22, 40, 54, 56, 45, 85, 93, 79, 60, 3, 47, 5, 16, 76, 36, 57, 24, 6, 39, 28, 49, 4, 96, 90, 55, 26, 91, 31, 99, 67, 43, 51, 34, 70, 48, 82, 58], 'distribution_center': {'name': 'Academy & Flintridge-Colorado Spri', 'url': 'https://www.starbucks.com/store-locator/store/10317', 'street_address': '4825 Academy Blvd N', 'city': 'Colorado Springs', 'zip_code': '809184121', 'country_code': 'US', 'country': 'United States', 'open_hours': 'Wednesday : 5:30 AM to 8:30 PM, Thursday : 5:30 AM to 8:30 PM, Thursday : 5:30 AM to 8:30 PM, Friday : 5:30 AM to 10:00 PM, Saturday : 5:30 AM to 9:30 PM, Sunday : 5:30 AM to 9:30 PM, Monday : 5:30 AM to 8:30 PM', 'latitude': 38.902276, 'longitude': -104.768681}}


In [ ]:
article_info = {}
for country_code in country_codes:
    word_list, word_cnt = article(country_code)
    article_info[country_code] = {"word_list": word_list, "word_cnt": word_cnt}
    display_wordcloud(word_list, country_code)

In [ ]:
def KMPSearch(pat, txt):
    visited= False
    count = 0
    # global count
    M = len(pat)
    N = len(txt)

    # create lps[] that will hold the longest prefix suffix
    # values for pattern
    lps = [0]*M
    j = 0  # index for pat[]

    # Preprocess the pattern (calculate lps[] array)
    computeLPSArray(pat, M, lps)

    if M == N:
        i = 0  # index for txt[]
        while i < N:
            if pat[j] == txt[i]:
                i += 1
                j += 1

            if j == M:
                #print ("Found pattern at index", str(i-j))
                j = lps[j-1]
                count = count+1
                visited=True

            # mismatch after j matches
            elif i < N and pat[j] != txt[i]:
                # Do not match lps[0..lps[j-1]] characters,
                # they will match anyway
                if j != 0:
                    j = lps[j-1]
                else:
                    i += 1
    return count,visited


def computeLPSArray(pat, M, lps):
    len = 0  # length of the previous longest prefix suffix

    lps[0]  # lps[0] is always 0
    i = 1

    # the loop calculates lps[i] for i = 1 to M-1
    while i < M:
        if pat[i] == pat[len]:
            len += 1
            lps[i] = len
            i += 1
        else:
            # This is tricky. Consider the example.
            # AAACAAAA and i = 7. The idea is similar
            # to search step.
            if len != 0:
                len = lps[len-1]

                # Also, note that we do not increment i here
            else:
                lps[i] = 0
                i += 1


def sentimentAnalysis(list, country):
    global pos_ranklist
    global neg_ranklist
    print(country)
    posper = positive(list)
    negper = negative(list)
    neutral(list,posper,negper)
    if posper > negper:
        print("Overall positive \n")
        pos_ranklist.append(posper[0])

    else:
        print('Overall negative \n')
        neg_ranklist.append(negper[0])

def ranking(r1, r2):
    ranking=[]

    r1.sort(reverse = True)
    r2.sort()
    ranking=r1+r2
    print(ranking)
    print(ranking[:3])

def positive(list):
    pos = open("./content/Positive.txt", encoding="utf8")
    pos = pos.read().splitlines()
    pos_count = 0
    for x in range(len(list)):
        for y in range(len(pos)):
            pos_count = pos_count + KMPSearch(pos[y], list[x])[0]
            #if (KMPSearch(pos[x], list[y])[1])== True:
            #    print(y)
    #print("Positive counts:", pos_count)
    posper = (pos_count/(len(list))*100)
    print("Positive Percentage: {:.2f}%" .format(posper))

    return posper, pos_count


def negative(list):
    neg = open("./content/Negative.txt", encoding="utf8")
    neg = neg.read().splitlines()
    neg_count = 0
    for x in range(len(list)):
        for y in range(len(neg)):
            neg_count = neg_count + KMPSearch(neg[y], list[x])[0]
            #if (KMPSearch(neg[x], list[y])[1])== True:
            #  list= list.pop(y)
    #print("Negative counts:", neg_count)
    negper = (neg_count/(len(list))*100)
    print("Negative Percentage: {:.2f}%" .format(negper))

    return negper, neg_count

def neutral(list,p,n):
    neut_count= len(list)- p[1]- n[1]
    #print("Neutral counts:", neut_count)
    nuetper = (neut_count/(len(list))*100)
    print("Neutral Percentage: {:.2f}%" .format(nuetper))

In [ ]:
# Solved the bug
pos_ranklist=[]
neg_ranklist=[]

sentimentAnalysis(article_info["US"]["word_list"],'United States of America')
#sentimentAnalysis(all_lists_TL,'Thailand')
#sentimentAnalysis(all_lists_NZ,'New Zealand')
#sentimentAnalysis(all_lists_HK,'Hong Kong')
#sentimentAnalysis(all_lists_DB,'United Arab Emirates')

#print("Ranking:")
#ranking(pos_ranklist,neg_ranklist)

In [ ]:
{
    "positive_percent": 0,
    "negative_percent": 0,
    "neutral_percent": 0,
    "overall_sentiment": "negative"
}

In [ ]:
def sentimentAnalysis(word_list, country):
    global pos_ranklist
    global neg_ranklist
    print(country)
    posper = positive(list)
    negper = negative(list)
    neutral(list,posper,negper)
    if posper > negper:
        print("Overall positive \n")
        pos_ranklist.append(posper[0])

    else:
        print('Overall negative \n')
        neg_ranklist.append(negper[0])